In [2]:
import pandas as pd
from ast import literal_eval
import numpy as np
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
from statistics import mean, median
import scipy
from sklearn.decomposition import PCA
from sklearn import preprocessing
from gprofiler import GProfiler
import warnings
warnings.filterwarnings('ignore')
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
figure(num=None, figsize=(8, 6), dpi=80, facecolor='w', edgecolor='k')
import operator
import qvalue as qv


#Reactome file containing information on pathways, the genes they contain and pathway name, also including the illumina identifier for the genes.

reactome = pd.read_csv('../data/reactome.csv', sep=',', index_col = 0)

def read_reactome(file_name, gene_name_start = "ENSG0"):
    df = pd.read_csv(file_name, sep='\t', header=None)
    
    if gene_name_start == None:
        sub_df = df
    else:
        subset_vec = df[0].str.startswith(gene_name_start)
        sub_df = df.loc[subset_vec]
    
    genes_df = sub_df.groupby(1)[0].apply(list)
    names_df = sub_df.groupby(1)[3].max()
    
    out_df = pd.concat([genes_df,names_df], axis=1)
    out_df.columns = ['genes', 'pathway_name']
    
    return out_df

low_level = read_reactome('../data/Ensembl2Reactome_All_Levels.txt.gz')

def my_pca(df, n_pc=1, normalize=True):
    df = df.dropna(axis = 0, how = 'all')#redundant, but keeping it just in case
    X = df.values.T
    if normalize:
        X2 = preprocessing.scale(X)
    else:
        X2 = X
    pca = PCA(n_components = n_pc)
    pca.fit(X2)
    my_pca.pca = pca  #needed for components
    Xnew = pca.fit_transform(X2)
    out_df = pd.DataFrame(Xnew.transpose(), index=list(range(1,n_pc+1)), columns=df.columns)
    out_df = out_df.transpose()
    
    return out_df, my_pca.pca.components_, my_pca.pca.explained_variance_ratio_

#Importing metabric dataset, dividing up what is clinical/expression data and changing the type of the expression columns to float
metabric_data = pd.read_csv('../data/metabric.csv.gz')
#clinical_data = metabric_data.iloc[:27, :]
expression_data = metabric_data.iloc[27:,:]

#print(expression_data.columns)
dtypedict = {}
for i in expression_data.columns[1:]:
    dtypedict[i] = 'float32'
expression_data = expression_data.astype(dtypedict)



new_clinical_patient = pd.read_csv('../data/data_clinical_patient.txt', sep='\t', index_col=0).iloc[4:]
new_clinical_sample = pd.read_csv('../data/data_clinical_sample.txt', sep='\t', index_col=0).iloc[4:]
new_clinical = pd.concat([new_clinical_patient, new_clinical_sample.reindex(new_clinical_patient.index)], axis=1)
new_clinical['Triple Neg'] = new_clinical.apply(lambda row: True if ((row['ER Status'] == 'Negative') 
                                                                     and (row['PR Status'] == 'Negative') 
                                                                     and (row['HER2 Status'] == 'Negative')) else False, axis = 1)

new_clinical['ER-/PR-/HER2+'] = new_clinical.apply(lambda row: True if ((row['ER Status'] == 'Negative') 
                                                                     and (row['PR Status'] == 'Negative') 
                                                                     and (row['HER2 Status'] == 'Positive')) else False, axis = 1)





genes = expression_data['Unnamed: 0'].values.tolist()

gp = GProfiler(return_dataframe = True)
gp = gp.convert(organism='hsapiens',
          query=genes)

gp = gp.loc[gp['n_converted'] == 1]
gp = gp.loc[gp['name'] != 'None']
gp = gp.set_index('incoming')
gprofiler_names = gp
gprofiler_names

dataset = expression_data.set_index('Unnamed: 0') #gene_patient
pca_per_pathway = pd.DataFrame(index=expression_data.columns)

real_gene_names = pd.read_csv('../data/illumina2symbol.txt', sep="\t", index_col = 0)



In [3]:
genes_components_per_pathway = {} #nested dictionary where the 'outer dictionary' is the pathway names as keys and values are 
                                  #another dictionary with genes as keys and components as values

for pathway in reactome.index:
    genes = reactome.loc[pathway, "illumina"]
    genes = literal_eval(genes)
    genes = list(filter(lambda a: a != 'NaN', genes))
    pathwaydata = dataset.loc[genes]
    if pathwaydata.index.empty == True:
        pass
    else:
        pathwaydata = pathwaydata.dropna(axis = 0, how = 'any') #has to be done so the lists match, this makes the dropna in my_pca function obsolete
        presentgenes = pathwaydata.index.values.tolist()
        if len(presentgenes) <= 1:
            pass
        else:
            res, components, explained_variance = my_pca(pathwaydata)
            print(res)
            pathwayname = reactome.loc[pathway, 'pathway_name']
            pca_per_pathway[pathwayname] = res

            components = components.tolist()[0]
            innerdict = {}
            for i in range(0, len(presentgenes)):
                component = components[i]
                gene = genes[i]
                if gene in real_gene_names.index:
                    real_name = real_gene_names.loc[gene, "symbol"]
                    innerdict[real_name] = component
                elif gene in gprofiler_names.index:
                    real_name = gprofiler_names.loc[gene, 'name']
                    innerdict[real_name] = component
                else:
                    innerdict[gene] = component
            sorted_innerdict = sorted(innerdict.items(), key = operator.itemgetter(1), reverse = True)
            genes_components_per_pathway[pathwayname] = [sorted_innerdict, explained_variance.flat[0]]

pca_per_pathway = pca_per_pathway.iloc[1:]

                1
MB-0002 -0.464913
MB-0008  1.135677
MB-0010 -0.016406
MB-0035 -0.045984
MB-0036 -1.107910
MB-0050  1.003818
MB-0059 -0.473150
MB-0060  0.681486
MB-0066  0.539735
MB-0101  1.391563
MB-0102  0.975991
MB-0106 -1.716131
MB-0112  0.721623
MB-0115  2.891248
MB-0117 -1.218243
MB-0119  0.324922
MB-0120 -1.282449
MB-0121  0.066524
MB-0122  0.241646
MB-0123  0.632205
MB-0126  0.430240
MB-0131  0.059170
MB-0133 -0.570782
MB-0135 -0.117803
MB-0136  0.874496
MB-0138  1.158646
MB-0139  2.100204
MB-0140 -0.166481
MB-0142 -0.881733
MB-0143  0.237474
...           ...
MB-7264  0.052616
MB-7266 -2.427948
MB-7267  1.027191
MB-7268  0.899953
MB-7269 -1.542249
MB-7270 -0.818144
MB-7273  0.133795
MB-7275  0.119508
MB-7276  1.452774
MB-7277 -0.836269
MB-7278 -0.750752
MB-7279 -0.591865
MB-7280  3.168237
MB-7281 -0.708823
MB-7283 -1.524783
MB-7284 -1.585520
MB-7285  2.112240
MB-7286  0.464740
MB-7287 -0.461482
MB-7288  0.084161
MB-7289  0.948163
MB-7291  1.676027
MB-7292 -0.991137
MB-7293  0

                1
MB-0002  4.655565
MB-0008  8.272937
MB-0010  5.898240
MB-0035  0.494914
MB-0036  4.147963
MB-0050 -1.933751
MB-0059  0.905942
MB-0060 -1.130984
MB-0066 -1.228740
MB-0101  6.086674
MB-0102  3.120504
MB-0106  2.340541
MB-0112  6.462937
MB-0115  3.692863
MB-0117 -0.745160
MB-0119  7.126933
MB-0120  8.332044
MB-0121  1.312075
MB-0122  1.857700
MB-0123  6.007672
MB-0126  6.382888
MB-0131  1.849582
MB-0133 -3.666939
MB-0135  0.420731
MB-0136 -4.222500
MB-0138  1.301519
MB-0139 -2.491193
MB-0140  2.869867
MB-0142  4.153458
MB-0143  1.076458
...           ...
MB-7264  3.076342
MB-7266  7.640172
MB-7267  4.764861
MB-7268  0.048722
MB-7269  2.775679
MB-7270  9.691807
MB-7273 -0.342198
MB-7275  0.164048
MB-7276 -2.698674
MB-7277 -1.550793
MB-7278  0.962202
MB-7279 -2.671316
MB-7280  3.281409
MB-7281 -1.002801
MB-7283 -2.440549
MB-7284 -3.839314
MB-7285  4.370538
MB-7286 -2.683913
MB-7287  2.022611
MB-7288  3.261115
MB-7289 -0.795145
MB-7291 -1.753838
MB-7292  6.284089
MB-7293 -1

                1
MB-0002 -2.220945
MB-0008  0.153180
MB-0010  0.303375
MB-0035  2.075835
MB-0036 -1.113195
MB-0050  0.209961
MB-0059 -0.527548
MB-0060  2.052147
MB-0066 -1.904882
MB-0101 -0.184899
MB-0102 -0.663025
MB-0106  0.175600
MB-0112 -0.865113
MB-0115  1.427468
MB-0117  0.003445
MB-0119 -0.571144
MB-0120  1.425543
MB-0121 -0.538211
MB-0122 -0.525548
MB-0123  0.126102
MB-0126 -0.536483
MB-0131  1.160220
MB-0133 -0.263440
MB-0135 -0.859858
MB-0136 -0.988820
MB-0138 -0.812007
MB-0139  0.531182
MB-0140 -1.948142
MB-0142 -1.997516
MB-0143  0.668133
...           ...
MB-7264  0.350254
MB-7266 -1.070970
MB-7267  1.255828
MB-7268 -0.360654
MB-7269  1.453831
MB-7270  0.581457
MB-7273  2.136531
MB-7275  0.521201
MB-7276 -0.749928
MB-7277 -1.565716
MB-7278 -0.407212
MB-7279  1.296026
MB-7280 -1.638602
MB-7281  1.619073
MB-7283 -0.456304
MB-7284  0.417706
MB-7285 -0.552313
MB-7286 -0.247645
MB-7287  0.136364
MB-7288  0.794137
MB-7289  0.196396
MB-7291  0.583290
MB-7292 -1.476348
MB-7293 -1

                1
MB-0002 -0.383060
MB-0008 -0.986897
MB-0010 -0.905870
MB-0035  0.612568
MB-0036  1.082351
MB-0050  0.827492
MB-0059  1.051291
MB-0060 -2.275640
MB-0066  0.788804
MB-0101  0.616673
MB-0102 -0.470973
MB-0106  1.140402
MB-0112  1.543797
MB-0115 -2.638027
MB-0117 -1.254884
MB-0119  0.431868
MB-0120 -0.827366
MB-0121 -1.690253
MB-0122 -1.048007
MB-0123 -1.964891
MB-0126  0.533493
MB-0131 -1.314814
MB-0133  0.669430
MB-0135  1.125662
MB-0136  0.600513
MB-0138 -0.317776
MB-0139  0.970433
MB-0140 -1.190500
MB-0142  0.262891
MB-0143 -0.646836
...           ...
MB-7264  0.460291
MB-7266  1.354036
MB-7267 -0.421020
MB-7268 -0.959276
MB-7269 -0.799535
MB-7270 -1.303250
MB-7273 -0.664230
MB-7275 -0.621270
MB-7276  2.040267
MB-7277 -1.469255
MB-7278  0.299075
MB-7279  1.147920
MB-7280 -0.042830
MB-7281 -2.834294
MB-7283  2.032388
MB-7284  0.821415
MB-7285  0.132353
MB-7286 -0.722727
MB-7287 -0.576108
MB-7288 -1.216295
MB-7289  0.303752
MB-7291 -3.361448
MB-7292 -1.114332
MB-7293 -0

                1
MB-0002 -0.839519
MB-0008 -0.334564
MB-0010 -1.017349
MB-0035 -0.489386
MB-0036  6.001373
MB-0050 -0.832339
MB-0059 -1.058254
MB-0060 -1.099524
MB-0066 -0.664844
MB-0101 -1.039093
MB-0102 -1.998163
MB-0106 -0.992357
MB-0112 -0.109019
MB-0115 -1.512002
MB-0117 -0.405713
MB-0119  1.262311
MB-0120 -3.317290
MB-0121  1.460357
MB-0122 -1.237321
MB-0123 -2.079921
MB-0126  0.711437
MB-0131  0.670821
MB-0133  0.393978
MB-0135  0.060545
MB-0136 -0.836376
MB-0138 -0.511520
MB-0139 -0.013210
MB-0140 -0.736879
MB-0142  1.861163
MB-0143 -1.114713
...           ...
MB-7264  0.191734
MB-7266  7.297694
MB-7267 -0.357693
MB-7268 -1.078855
MB-7269 -1.592299
MB-7270 -0.346895
MB-7273 -1.093076
MB-7275 -1.646449
MB-7276 -0.545842
MB-7277 -0.094396
MB-7278 -2.002815
MB-7279  1.102092
MB-7280 -1.469291
MB-7281 -1.239579
MB-7283 -0.254650
MB-7284  0.706302
MB-7285 -2.099957
MB-7286  0.752678
MB-7287 -1.247703
MB-7288 -0.744082
MB-7289 -1.479417
MB-7291 -1.963409
MB-7292  3.262930
MB-7293 -1

...

                1
MB-0002 -0.066751
MB-0008 -0.707654
MB-0010  0.981738
MB-0035  0.563124
MB-0036  0.056668
MB-0050 -0.368492
MB-0059 -0.372932
MB-0060 -0.394453
MB-0066  0.502119
MB-0101 -1.026722
MB-0102 -0.734612
MB-0106  0.472311
MB-0112 -1.370067
MB-0115 -0.905843
MB-0117 -0.121076
MB-0119 -0.416085
MB-0120 -0.366520
MB-0121  0.189822
MB-0122  0.160486
MB-0123  0.574067
MB-0126 -0.793297
MB-0131  0.148435
MB-0133 -4.457083
MB-0135 -0.802384
MB-0136 -0.936826
MB-0138 -1.160224
MB-0139 -1.472889
MB-0140  0.347900
MB-0142  0.552487
MB-0143  0.205635
...           ...
MB-7264 -0.675160
MB-7266  1.964212
MB-7267 -0.291931
MB-7268  0.738587
MB-7269  2.390438
MB-7270  3.287608
MB-7273 -0.159832
MB-7275 -0.368933
MB-7276 -0.183986
MB-7277  0.650010
MB-7278  0.947673
MB-7279 -1.548732
MB-7280  0.587723
MB-7281  0.323011
MB-7283  0.180581
MB-7284 -0.428158
MB-7285  0.762978
MB-7286 -0.838388
MB-7287 -1.477247
MB-7288  0.588072
MB-7289 -2.679451
MB-7291  0.187250
MB-7292 -0.875251
MB-7293 -0

                1
MB-0002  1.419701
MB-0008 -2.500869
MB-0010 -1.972940
MB-0035  2.204586
MB-0036  0.704488
MB-0050 -1.644301
MB-0059 -1.529197
MB-0060 -2.763116
MB-0066 -1.909586
MB-0101 -1.632994
MB-0102 -0.078784
MB-0106  1.310974
MB-0112 -0.858506
MB-0115 -2.796802
MB-0117  0.433250
MB-0119 -0.094953
MB-0120 -0.660817
MB-0121 -2.315866
MB-0122 -0.894492
MB-0123 -0.889130
MB-0126 -2.388264
MB-0131 -2.293792
MB-0133  0.338749
MB-0135 -0.434712
MB-0136 -2.096850
MB-0138 -0.183788
MB-0139 -2.178922
MB-0140 -0.899066
MB-0142  1.014210
MB-0143 -0.299661
...           ...
MB-7264  0.822563
MB-7266  2.322142
MB-7267 -1.291415
MB-7268  0.811228
MB-7269 -0.812335
MB-7270  0.256100
MB-7273 -5.701236
MB-7275 -3.763149
MB-7276  1.895341
MB-7277  1.965270
MB-7278  4.709312
MB-7279  2.390353
MB-7280  1.105658
MB-7281 -0.397399
MB-7283  2.364781
MB-7284  1.152423
MB-7285 -4.261975
MB-7286 -1.011747
MB-7287 -2.824626
MB-7288 -0.280528
MB-7289 -3.605089
MB-7291 -4.478319
MB-7292 -1.071315
MB-7293 -1

                 1
MB-0002  -6.514254
MB-0008   2.918535
MB-0010  -6.083162
MB-0035 -11.203477
MB-0036  -1.623363
MB-0050  -9.939184
MB-0059   1.246990
MB-0060  -1.945295
MB-0066   5.389663
MB-0101  -2.941783
MB-0102   2.662352
MB-0106  -2.931192
MB-0112   7.579087
MB-0115  -1.359990
MB-0117  -8.828996
MB-0119  -7.792058
MB-0120  -8.552711
MB-0121  -8.719597
MB-0122  -7.534979
MB-0123 -12.475082
MB-0126   4.303209
MB-0131  -0.511533
MB-0133  -2.510221
MB-0135  -2.458233
MB-0136  -2.606707
MB-0138   2.254779
MB-0139  -1.158717
MB-0140  -2.893035
MB-0142   7.895599
MB-0143  -7.987305
...            ...
MB-7264   2.565986
MB-7266  -9.934912
MB-7267  -1.467701
MB-7268  -3.251402
MB-7269   0.521767
MB-7270  -1.013031
MB-7273  -2.144907
MB-7275   0.199512
MB-7276   3.287688
MB-7277 -10.111168
MB-7278  -2.989700
MB-7279  17.722380
MB-7280 -10.115478
MB-7281   6.971596
MB-7283  -4.210506
MB-7284  -1.682372
MB-7285  -6.682725
MB-7286   4.456866
MB-7287   2.504154
MB-7288  -0.829511
MB-7289 -11.

                 1
MB-0002  -0.181209
MB-0008  -6.103691
MB-0010  -4.429469
MB-0035   2.307185
MB-0036   0.652173
MB-0050  -1.234763
MB-0059  -4.292345
MB-0060  -7.273607
MB-0066  -7.044347
MB-0101  -1.349735
MB-0102  -3.961126
MB-0106   2.509515
MB-0112  -3.463129
MB-0115  -5.246091
MB-0117   0.818815
MB-0119  -2.911410
MB-0120  -1.535758
MB-0121  -6.407045
MB-0122  -4.043545
MB-0123  -9.242504
MB-0126  -0.852169
MB-0131  -1.802844
MB-0133   2.981786
MB-0135  -3.796854
MB-0136  -5.329268
MB-0138   2.631019
MB-0139  -0.110125
MB-0140  -1.463623
MB-0142   1.139713
MB-0143  -1.103450
...            ...
MB-7264   2.978940
MB-7266   0.236273
MB-7267   1.234850
MB-7268  -2.645636
MB-7269  -2.246198
MB-7270   0.104618
MB-7273  -6.583871
MB-7275  -6.027480
MB-7276  -0.924476
MB-7277  -2.903471
MB-7278   2.780069
MB-7279   7.453156
MB-7280   0.306341
MB-7281   0.093177
MB-7283   5.662925
MB-7284  -0.075521
MB-7285  -5.234860
MB-7286  -2.372419
MB-7287  -7.005774
MB-7288  -9.528714
MB-7289  -5.

                1
MB-0002 -1.718513
MB-0008  0.911410
MB-0010 -1.831639
MB-0035  2.369227
MB-0036 -1.141991
MB-0050  1.390615
MB-0059  1.175209
MB-0060  0.211781
MB-0066 -0.615682
MB-0101 -2.617655
MB-0102 -3.004807
MB-0106  1.725542
MB-0112 -1.900308
MB-0115  1.017736
MB-0117  1.396359
MB-0119 -2.474471
MB-0120 -1.412309
MB-0121 -2.393811
MB-0122 -0.132895
MB-0123 -3.345698
MB-0126  0.015671
MB-0131 -0.520470
MB-0133  2.628673
MB-0135 -2.965669
MB-0136 -2.120229
MB-0138  1.111473
MB-0139  1.756201
MB-0140 -4.762919
MB-0142 -0.582879
MB-0143 -0.254647
...           ...
MB-7264 -1.209305
MB-7266  0.316527
MB-7267 -3.890249
MB-7268  0.841504
MB-7269  0.578354
MB-7270 -2.605367
MB-7273 -2.158524
MB-7275 -2.593170
MB-7276 -1.464331
MB-7277 -1.670094
MB-7278 -1.164354
MB-7279  2.362298
MB-7280 -2.486320
MB-7281  0.122075
MB-7283  2.586257
MB-7284  3.582648
MB-7285 -3.616637
MB-7286  1.824791
MB-7287 -2.428677
MB-7288 -3.187387
MB-7289 -2.264115
MB-7291 -3.730552
MB-7292 -4.864974
MB-7293 -4

In [6]:
mutation_df.shape

(2369, 173)

In [5]:
mutation_df = pd.read_csv("../data/mutations_per_patients.csv", sep=",", index_col = 0)

In [7]:
full_df = pd.concat([pca_per_pathway, mutation_df.reindex(pca_per_pathway.index)], axis= 1)
full_df
mutations = full_df.iloc[:,-173:]

In [8]:
from scipy.stats import ttest_ind, mannwhitneyu
import qvalue as qv

clusterframes = {}



for column in mutations:
    #mutated_gene = mutations[column]
    grouped_by_cluster = full_df.groupby(column)
    for group in grouped_by_cluster:
        df_cluster = pd.DataFrame(index=full_df.iloc[:,:-173].columns)
        groupname = group[0]
        df = group[1].iloc[:,:-173]
        group2_df = full_df[full_df[column] != groupname].iloc[:,:-173]
        pvaluelist = []
        group1_mean_list = []
        group2_mean_list = []
        for pathway in df:
            group = df[pathway]
            group2 = group2_df[pathway]
            test = mannwhitneyu(group, group2)
            pvaluelist.append(test[1])
            group_mean = group.mean()
            group1_mean_list.append(group_mean)
            group2_mean = group2.mean()
            group2_mean_list.append(group2_mean) 
        
    
    df_cluster[f'{groupname}'] = group1_mean_list
    df_cluster['Other samples'] = group2_mean_list
    df_cluster['Fold Change'] = np.log2(abs(df_cluster[f'{groupname}'])) - np.log2(abs(df_cluster['Other samples']))
    
    
    df_cluster['p-values'] = pvaluelist
    qv.qvalues(df_cluster, 'p-values', f'{groupname} qvalues')
    df_cluster['p-values'] = -np.log10(df_cluster['p-values'])
    df_cluster[f'{groupname} qvalues'] = -np.log10(df_cluster[f'{groupname} qvalues'])
    print(column)
    clusterframes[column] = [df_cluster, mutations[column].value_counts()]
    #clusterframes[column] = df_cluster

        
clusterframes

TP53
MLLT4
NF2
SF3B1
NT5E
EGFR
PRKCQ
AHNAK
CLK3
ERBB2
MUC16
EP300
HIST1H2BC
UBR5
USP28
AHNAK2
BIRC6
PIK3CA
MAP3K13
COL12A1
FOXO3
SYNE1
NRG3
DNAH2
NF1
SETDB1
COL6A3
ATR
KMT2C
GPR124
ARID2
ERBB3
SIK1
TAF1
PTEN
AKT1
FANCA
MLL2
BRCA1
DNAH11
AKAP9
STAB2
HERC2
CACNA2D3
RYR2
PALLD
ARID1A
LAMB3
SBNO1
NCOA3
STK11
MAP3K1
PIK3R1
UTRN
TG
HRAS
FANCD2
SHANK2
NPNT
USH2A
PBRM1
CDH1
MYH9
MAP2K4
NCOR1
PTPRD
TBX3
CBFB
CTCF
RUNX1
COL22A1
NCOR2
DNAH5
GATA3
AFF2
ALK
MAP3K10
BRCA2
KDM3A
FAM20C
MAGEA8
L1CAM
PRKCZ
GPS2
USP9X
PTPN22
PDE4DIP
GPR32
LARGE
THSD7A
SIAH1
LAMA2
HDAC9
ARID1B
FLT3
PRKCE
AGTR2
PTPRM
CTNNA3
CTNNA1
ROS1
RPGR
PRR16
ASXL1
SETD1A
AKT2
MBL2
GH1
SGCD
KDM6A
BRAF
CASP8
SETD2
SMARCC1
NR3C1
DCAF4L2
MYO1A
CHEK2
KRAS
LIFR
DTWD2
NOTCH1
GLDC
THADA
PRPS2
FRMD3
MYO3A
ACVRL1
SMARCC2
TTYH1
FOXO1
OR6A2
APC
RB1
SMARCB1
CLRN2
MTAP
FBXW7
ARID5B
PRKACG
PRKG1
BCAS3
ZFP36L1
TBL1XR1
BAP1
SPACA1
JAK1
CHD1
FOXP1
ASXL2
AGMO
LIPI
SMAD4
BRIP1
ERBB4
MEN1
CDKN1B
CDKN2A
RASGEF1B
NDFIP1
PPP2R2A
SMAD2
SIK2
NEK1
SMARCD1
NR2F

{'TP53': [                                                          WT  Other samples  \
  Transcriptional Regulation by MECP2                -1.069762       1.641391   
  G1 Phase                                           -1.180159       1.810777   
  Cyclin D associated events in G1                   -1.180159       1.810777   
  DAG and IP3 signaling                               0.879302      -1.349156   
  Serine biosynthesis                                -0.629849       0.966409   
  SLC-mediated transmembrane transport               -1.824355       2.799202   
  Activation of AMPK downstream of NMDARs             0.914358      -1.402947   
  Metabolism of nucleotides                          -1.360173       2.086983   
  Activation of NMDA receptors and postsynaptic e...  1.127821      -1.730474   
  Post NMDA receptor activation events                1.102714      -1.691950   
  Ubiquinol biosynthesis                             -0.583281       0.894958   
  Nucleotide salvage

In [9]:
high_q = []
for mut in clusterframes:
    i = clusterframes[mut]
    if i[0].iloc[:1,4:].values[0][0] >= 10:
        print(mut)
        print(i[0].iloc[:1,4:].values[0][0]) #this is the q-value of the pathway with the highest q-value -_-
        high_q.append(mut)

TP53
140.57400760110372
PIK3CA
42.614925617620074
MAP3K1
11.341251936099614
CDH1
16.544582197862848
CBFB
13.248201260330292
GATA3
14.392987649195767


In [10]:
high_q_df = pd.DataFrame(index = clusterframes['TP53'][0].index)
for i in high_q:
    q_values = clusterframes[i][0].iloc[:,4:]
    high_q_df[i] = q_values

    
high_q_df.sort_values(by='CDH1', ascending = False)
high_q_df.to_csv('../exp/mutations_with_high_q.csv')
    

In [13]:
ER_Pos_driver_genes = ['PIK3CA', 'TP53', "GATA3", "CDH1", "MAP3K1",
                       "KMT2C", "AKT1", "CBFB", "RB1"]
BRCA_genes = ['BRCA1', "BRCA2"]

clusterframes['BRCA2']

[                                                          WT  Other samples  \
 Spry regulation of FGF signaling                    0.058107      -0.630874   
 Defective CYP11A1 causes Adrenal insufficiency,... -0.047314       0.513698   
 Sphingolipid de novo biosynthesis                   0.096352      -1.046112   
 Negative regulation of FGFR2 signaling              0.056177      -0.609918   
 Nuclear Events (kinase and transcription factor...  0.060463      -0.656457   
 ERK/MAPK targets                                    0.057848      -0.628060   
 ERKs are inactivated                                0.048255      -0.523906   
 Negative regulation of FGFR4 signaling              0.057284      -0.621943   
 MAPK targets/ Nuclear events mediated by MAP ki...  0.067023      -0.727674   
 Regulation of TP53 Activity                         0.142852      -1.550961   
 TP53 Regulates Transcription of Death Receptors...  0.044354      -0.481559   
 Processing of Intronless Pre-mRNAs     

In [14]:
high_q_df = pd.DataFrame(index = clusterframes['TP53'][0].index)
for i in ER_Pos_driver_genes:
    q_values = clusterframes[i][0].iloc[:,4:]
    high_q_df[i] = q_values
    
for i in BRCA_genes:
    q_values = clusterframes[i][0].iloc[:,4:]
    high_q_df[i] = q_values

In [15]:
high_q_df.to_csv('../exp/mutations_with_high_q.csv')